<img src="pic/ex01.png" width="100%"> <br>

<h1 class="jp-toc-ignore">ICON Training - Hands-on Session</h1>

# Optional Exercise 1: Tracer Advection

---

<figure style="float:right;">
<img src="pic/jw_initial_tracer_dist.png" width="700" alt="alt_text"/>
<figcaption style="text-align:center"><b>Vertical cross sections of predefined initial tracer distributions.</b></br> 
                                      <b>Tracer q3 only depends on the latitudinal position, while q4 is constant.</b> 
</figcaption>
</figure>

The Jablonowski-Williamson (JW) test case provides a set of four predefined tracer initial conditions which can be activated 
or deactivated via namelist (see the figure on the right). 
Here, you will learn **how to enable and control the transport of passive tracers** in an idealized test.
See the Tutorial book, Sections 4.2.2 and 3.6.5, for details on the configuration of the tracer transport for standard NWP runs.

For simplicity, we make use of the following scripts and namelists from the previous JW exercises:

* the master namelist file (**icon_master.namelist**)
* the model namelist file for the nested setup (**NAMELIST_NWP**)
* the ICON batch job (**icon.sbatch**)

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Setup):</b> 
    </br>
    Execute the following cell, in order to
    <ul>
        <li> set some environment variables for this exercise</li>
        <li> copy the reference scripts <b>icon_master.namelist</b>, <b>NAMELIST_NWP</b>, <b>icon.sbatch</b></li>
    </ul>
</div>

In [ ]:
# base directory for ICON sources and binary:
export ICONDIR=/pool/data/ICON/ICON_training/icon/

# directory with input grids:
export GRIDDIR=/pool/data/ICON/ICON_training/exercise_idealized/grids/

# absolute path to directory with plenty of space:
export SCRATCHDIR=/scratch/${USER::1}/$USER
export EXPDIR=$SCRATCHDIR/exercise_idealized/exp_JW_R02B04_adv
if [ ! -d $EXPDIR ]; then
    mkdir -p $EXPDIR
fi

# visualization settings
export SCRIPTDIR=$HOME/icon-training-scripts/exercise_idealized/plot_scripts

# copy prepared Namelists and batch script
cp /pool/data/ICON/ICON_training/exercise_idealized/NAMELIST_NWP $EXPDIR/
cp /pool/data/ICON/ICON_training/exercise_idealized/icon_master.namelist $EXPDIR/
cp /pool/data/ICON/ICON_training/exercise_idealized/icon.sbatch $EXPDIR/

# grid files: link to experiment directory
ln -sf ${GRIDDIR}/icon_grid_00*.nc ${EXPDIR}/.

In the above settings we used the `scratch` partition of the file system, with a quota of 15 TiB (see `/sw/bin/lfsquota.sh -u $USER`).

###

In the namelist file **NAMELIST_NWP** we have omitted the namelists `run_nml`, `nh_testcase_nml` and the output namelists `output_nml`, as we are going to recreate them for a setup with tracers.

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Enabling the transport of one or more passive tracers):</b>
    </br>
    In order to enable tracer advection for the JW test, adapt the namelist settings in the cell below as follows:
    <ul>
        <li>Enable the transport module by activating the main switch <code>ltransport (run_nml)</code></li>
        <li>Select the tracers number $1$ and $4$ (or all, if you like) from the set of pre-defined tracer distributions depicted in the figure above.
            A specific tracer is selected by adding the respective tracer number (1,2,3, or 4) to the namelist variable <code>tracer_inidist_list (nh_testcase_nml)</code>.</li>
         <li>Set the total number of tracer fields <code>ntracer (run_nml)</code> accordingly.</li>
         <li>Enable (uncomment) the namelist <code>transport_nml</code>, which specifies details of the applied numerical transport schemes and limiters.</li>
    </ul>
</div>

In [ ]:
cat >> $EXPDIR/NAMELIST_NWP << EOF

! run_nml: general switches ---------------------------------------------------
&run_nml
 ltestcase                   =                       .TRUE.       ! idealized testcase runs
 num_lev                     =                    40,40,40        ! number of full levels (atm.) for each domain
 lvert_nest                  =                      .FALSE.       ! vertical nesting
 dtime                       =                       1440.        ! timestep in seconds
 ldynamics                   =                      .TRUE.        ! compute adiabatic dynamic tendencies
 ltransport                  =                 ??????????         ! main switch for large-scale tracer transport
 ntracer                     =                 ??????????         ! number of advected tracers
 iforcing                    =                          0         ! pure dynamics (no physics forcing)
 msg_level                   =                         10         ! controls how much printout is written during runtime
 ltimer                      =                     .FALSE.        ! timer for monitoring the runtime of specific routines
 output                      =                       "nml"        ! main switch for enabling/disabling components of the model output
/

! nh_testcase_nml: idealized testcase specification --------------------------
&nh_testcase_nml
 nh_test_name                =                        "jabw"      ! testcase selection
 jw_up                       =                          1.0       ! amplitude of u-perturbation [m/s]
 tracer_inidist_list         =                 ??????????         ! choosing from a list of predefined tracer distributions
/

! transport_nml: tracer transport ---------------------------------------------
!&transport_nml
! ivadv_tracer                =                 3, 3, 3, 3         ! tracer specific method to compute vertical advection
! ihadv_tracer                =                 2, 2, 2, 2         ! tracer specific method to compute horizontal advection
! itype_hlimit                =                 0, 0, 0, 0         ! type of limiter for horizontal transport
! itype_vlimit                =                 0, 0, 0, 0         ! type of limiter for horizontal transport
! beta_fct                    =                          1.005     ! factor of allowed over-/undershooting in monotonous limiter
!/
EOF

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Extend the output namelist):</b>
    <ul>
        <li>Add the selected tracers to the list of pressure level and model level output fields in the namelist <code>output_nml</code></li>
    </ul>
    <b>Note:</b> In idealized tests, tracers are named <code>qx</code>, where <code>x</code> is a number indicating the position of the tracer within the ICON-internal 4D tracer memory.</br> 
    For this testcase, tracer 1 is named <code>q1</code>, and so on.</br>
    These default names can be overwritten with the namelist variable <code>tracer_names (transport_nml)</code>. See Section 4.2.2 of the tutorial for details. 
</div>

In [ ]:
cat >> $EXPDIR/NAMELIST_NWP << EOF

! output_nml: specifies an output stream --------------------------------------
! model level output on native (triangular) grid
&output_nml
 filetype                    =                          4         ! output format: 2=GRIB2, 4=NETCDFv2
 dom                         =                         -1         ! write all domains
 output_bounds               =       0., 10000000., 86400.        ! output: start, end, increment
 steps_per_file              =                         30         ! number of output steps in one output file
 mode                        =                          1         ! 1: forecast mode (relative t-axis), 2: climate mode (absolute t-axis)
 include_last                =                      .TRUE.        ! flag whether to include the last time step
 output_filename             =                   'exp3_JW'        ! file name base
 output_grid                 =                      .TRUE.        ! flag whether grid information is added to output.
 !
 ml_varlist                  =  'u', 'v', 'w', 'temp', 'pres','topography_c', 'pres_sfc', 'vor', 'div', ?????????
/

! output_nml: specifies an output stream --------------------------------------
! pressure level output on native grid
&output_nml
 filetype                    =                          4         ! output format: 2=GRIB2, 4=NETCDFv2
 dom                         =                         -1         ! write all domains
 output_bounds               =       0., 10000000., 86400.        ! output: start, end, increment
 steps_per_file              =                         30         ! number of output steps in one output file
 mode                        =                          1         ! 1: forecast mode (relative t-axis), 2: climate mode (absolute t-axis)
 include_last                =                      .TRUE.        ! flag whether to include the last time step
 output_filename             =                   'exp3_JW'        ! file name base
 output_grid                 =                      .TRUE.        ! flag whether grid information is added to output.
 remap                       =                          0         ! no remapping (native grid)
 !
 pl_varlist                  =  'temp', 'vor', 'div', ?????????
 p_levels                    =  50000.,60000.,70000.,85000.,92500. ! pressure levels in Pa
/

! output_nml: specifies an output stream --------------------------------------
! model level output on regular lat/lon grid
&output_nml
 filetype                    =                          4         ! output format: 2=GRIB2, 4=NETCDFv2
 dom                         =                         -1         ! write all domains
 output_bounds               =       0., 10000000., 86400.        ! output: start, end, increment
 steps_per_file              =                         30         ! number of output steps in one output file
 mode                        =                          1         ! 1: forecast mode (relative t-axis), 2: climate mode (absolute t-axis)
 include_last                =                      .TRUE.        ! flag whether to include the last time step
 output_filename             =            'exp3_JW_lonlat'        ! file name base
 output_grid                 =                      .TRUE.        ! flag whether grid information is added to output.
 remap                       =                          1         ! remap to regular lat/lon grid
 reg_lat_def                 =                -90.,1.0,90.        ! start, increment, end latitude in degrees                 
 reg_lon_def                 =                 0.,1.0,359.0       ! start, increment, end longitude in degrees
 !
 ml_varlist                  =  'u', 'v', 'w', 'temp', 'pres','topography_c', 'pres_sfc', 'vor', 'div', ??????????
/
EOF

<details>
<summary style="font-size: 1.1em;">Solution</summary>
<pre>

&run_nml
 ltransport                  =                      .TRUE.        ! main switch for large-scale tracer transport
 ntracer                     =                          4         ! number of advected tracers

! nh_testcase_nml: idealized testcase specification --------------------------
&nh_testcase_nml
 nh_test_name                =                        "jabw"      ! testcase selection
 jw_up                       =                          1.0       ! amplitude of u-perturbation [m/s]
 tracer_inidist_list         =                 1, 2, 3, 4         ! choosing from a list of predefined tracer distributions
/

! transport_nml: tracer transport ---------------------------------------------
&transport_nml
 tracer_names                =                'q1','q2','q3','q4'
 ivadv_tracer                =                 3, 3, 3, 3         ! tracer specific method to compute vertical advection
 ihadv_tracer                =                 2, 2, 2, 2         ! tracer specific method to compute horizontal advection
 itype_hlimit                =                 4, 0, 0, 0         ! type of limiter for horizontal transport
 itype_vlimit                =                 3, 0, 0, 0         ! type of limiter for horizontal transport
 beta_fct                    =                          1.005     ! factor of allowed over-/undershooting in monotonous limiter
/

&output_nml 1
 ml_varlist                  =  'u', 'v', 'w', 'temp', 'pres','topography_c', 'pres_sfc', 'vor', 'div', 'q1', 'q2', 'q3', 'q4'

&output_nml 2
 pl_varlist                  =  'temp', 'vor', 'div', 'q1', 'q2', 'q3', 'q4'

&output_nml 3
 ml_varlist                  =  'u', 'v', 'w', 'temp', 'pres','topography_c', 'pres_sfc', 'vor', 'div', 'q1', 'q2', 'q3', 'q4'

</pre>
</details>

### Running the ICON model

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise:</b> 
    Submit the job script <b>icon.sbatch</b> to the HPC cluster, using the Slurm command <code>sbatch</code>.
</div>

In [ ]:
cd $EXPDIR && sbatch --account=$SLURM_JOB_ACCOUNT icon.sbatch

Check the job status using the Slurm command `squeue`

### Visualizaton

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Visualization):</b>
    </br>
    We suggest to have a look at the results using<code>ncview</code>, as it is useful to scan through different levels and time steps. To do so, please log in with your account <code>&dollar;USER@levante.dkrz.de</code> using your SSH client (e.g. PuTTY). After login, first load the <code>ncview</code> module: <code>module load ncview</code>.
    <ul>
        <li>Open the global domain output <code>&dollar;EXPDIR/exp3_JW_lonlat_DOM01_ML_0001.nc</code></li> 
        <li> Have a look at tracer number $4$.</br>
             Initially it is constant ($=1$) everywhere. Ideally, an initially constant tracer should stay constant for all times, no matter how complicated the flow.</li>
        <ul>
          <li> Does ICON preserve a constant tracer in a run <b>without</b> nest?</li>
          <li> Does ICON preserve a constant tracer in a run <b>with</b> nest?</br>
               Note: If a constant tracer is preserved in a two-way nested run, it is automatically preserved in a global run without nest (hence, a two-way nested run is sufficient to answer these questions).</li>
        </ul>
        <li>Have a look at tracer number $1$.</br> 
            The initial tracer values are in the range $0 \leq q1 \leq 0.98$. How do the global minimum and maximum values change as a function of time? Are they preserved?</li>
    </ul>
</div>

<details>
<summary style="font-size: 1.1em;">Solution</summary>
Answer:

Yes, the ICON transport is constancy preserving for the global domain as well as for nested domain(s). The given run is a two-way nested run, as can be inferred from the namelist variable lfeedback=.TRUE. (grid_nml). Hence the given run is sufficient to answer this question.

No, the global maximum and minimum values of q1 are not preserved over time. In particular the global minimum value falls below zero. The transport scheme is creating spurious undershoots (and overshoots) in the advected field.
</details>

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise (Avoiding non-physical overshoots and undershoots):</b>
    </br>
    Any higher-order transport scheme generates spurious overshoots and undershoots in the advected quantity. 
    In particular, undershoots can lead to numerical instabilities in real case NWP runs and must be avoided.
    <ul>
      <li>Have a look at tracer number 1. You will notice that spurious negative values emerge after some time.</li>
      <li>Activate an appropriate filter/limiter such that the transport scheme for tracer 1 becomes at least positive definite (i.e. $q(t)\geq 0 \,\, \forall\, t$). See the Tutorial book, Section 3.6.5, for additional help.</li>
      <li>Repeat the run to confirm that your settings are valid and document your settings below.</li>
    </ul>
</div>

Your answer:

`itype_hlimit` = ...  
`type_vlimit` = ...

<details>
<summary style="font-size: 1.1em;">Solution</summary>

Possible answer:  
`itype_hlimit` = 4, 0, 0, 0  
`type_vlimit` = 3, 0, 0, 0

</details>

---

<h2 class="jp-toc-ignore"> <b style="color:#2d4b9b;"> Congratulations! You have successfully completed optional Exercise 1.</b></h2>

---

## Further Reading and Resources

- ICON Tutorial, Ch. 4: <a href="https://www.dwd.de/DE/leistungen/nwv_icon_tutorial/nwv_icon_tutorial.html">https://www.dwd.de/DE/leistungen/nwv_icon_tutorial/nwv_icon_tutorial.html</a>
    <br/>A new <b>draft version</b> of the ICON Tutorial is available here: <a href="https://icon-training-2025-scripts-rendering-cc74a6.gitlab-pages.dkrz.de/index.html">https://icon-training-2025-scripts-rendering-cc74a6.gitlab-pages.dkrz.de/index.html</a>. It is currently being finalized and will be published soon.


---

*Author info: Deutscher Wetterdienst (DWD) 2025 ::  icon@dwd.de. For a full list of contributors, see CONTRIBUTING in the root directory. License info: see LICENSE file.*